## 

## Before starting - setup index

```
cd notebooks/elasticsearch/vmware
python extract_use_es.py 0    # base reindex step
python extract_use_es.py 1    # enrich with USE
python extract_use_es.py 2    # extract first line from raw text
```

In [1]:
from ltr.client import ElasticClient
client=ElasticClient()
vmware_corpus = client.to_dataframe(index='vmware')

Scanned 0 documents -- 0.5065471959999999
Scanned 1000 documents -- 1.0627588740000002
Scanned 2000 documents -- 1.5944322979999999
Scanned 3000 documents -- 2.239720869
Scanned 4000 documents -- 2.7512689010000004
Scanned 5000 documents -- 3.351753939
Scanned 6000 documents -- 3.8907507280000004
Scanned 7000 documents -- 4.509835361
Scanned 8000 documents -- 4.999324401
Scanned 9000 documents -- 5.5064347190000005
Scanned 10000 documents -- 5.990027322
Scanned 11000 documents -- 6.477529885
Scanned 12000 documents -- 6.942053797000001
Scanned 13000 documents -- 7.430488326
Scanned 14000 documents -- 7.906585606000001
Scanned 15000 documents -- 8.399952020999999
Scanned 16000 documents -- 8.915338293
Scanned 17000 documents -- 9.40125629
Scanned 18000 documents -- 9.869547534999999
Scanned 19000 documents -- 10.346141433
Scanned 20000 documents -- 10.811658015999999
Scanned 21000 documents -- 11.296199009999999
Scanned 22000 documents -- 11.771233223
Scanned 23000 documents -- 12.25925

Scanned 197000 documents -- 108.146897121
Scanned 198000 documents -- 108.630631236
Scanned 199000 documents -- 109.091732732
Scanned 200000 documents -- 109.583243845
Scanned 201000 documents -- 110.053421572
Scanned 202000 documents -- 110.573530818
Scanned 203000 documents -- 111.072509971
Scanned 204000 documents -- 111.579547619
Scanned 205000 documents -- 112.06593399
Scanned 206000 documents -- 112.575781126
Scanned 207000 documents -- 113.402635539
Scanned 208000 documents -- 113.969973197
Scanned 209000 documents -- 114.486139399
Scanned 210000 documents -- 114.975692444
Scanned 211000 documents -- 115.47554964
Scanned 212000 documents -- 116.061502475
Scanned 213000 documents -- 116.614003723
Scanned 214000 documents -- 118.760636638
Scanned 215000 documents -- 119.306226055
Scanned 216000 documents -- 119.803880136
Scanned 217000 documents -- 120.285093854
Scanned 218000 documents -- 120.790268079
Scanned 219000 documents -- 121.276351181
Scanned 220000 documents -- 121.7547

In [7]:
vmware_corpus.groupby('type')['type'].count()

type
Technical Article       255
concept              121436
reference             35837
task                  94459
troubleshooting        4807
Name: type, dtype: int64

In [14]:
type = 'concept'
for doc in vmware_corpus[vmware_corpus['type'] == 'task'].sample(frac=0.1).head().to_dict(orient='records'):
    print(doc['title'])
    print('--------')
    print(doc['first_line'])
    print('--------')
    print(doc['remaining_lines'])
    print('*********')

Install the NSX Manager Virtual Appliance
--------
The NSX Manager provides the graphical user interface (GUI) and the REST APIs for creating, configuring, and monitoring NSX components, such as controllers, logical switches, and edge services gateways.
--------
['The NSX Manager provides an aggregated system view and is the centralized network management component of NSX.', 'NSX Manager is installed as a virtual appliance on any ESX host in your vCenter environment.', 'The NSX Manager virtual machine is packaged as an OVA file, which allows you to use the vSphere Web Client to import the NSX Manager into the datastore and virtual machine inventory.', 'For high availability, VMware recommends that you deploy NSX Manager in a cluster configured with HA and DRS.', 'Optionally, you can install the NSX Manager in a different vCenter than the one that the NSX Manager will be interoperating with.', 'A single NSX Manager serves a single vCenter Server environment.', 'In cross-vCenter NSX inst

In [2]:
from ltr.client import ElasticClient
client=ElasticClient()

import pandas as pd
queries = pd.read_csv("data/test.csv")

def search(client, query):
    es = client.es
    body = {
        'size': 5,
        'query': {
            'bool': { 'should': [
                {'match_phrase': {
                    'remaining_lines': {
                        'slop': 10,
                        'query': query
                    }
                }},
                {'match_phrase': {
                    'first_line': {
                        'slop': 10,
                        'query': query
                    }
                }},
                {'match': {
                    'raw_text': {
                        'query': query
                    }
                }},
                {'match': {
                    'first_line': {
                        'query': query
                    }
                }},
            ]}
        }
    }
    return es.search(index='vmware', body=body)['hits']['hits']


def search_all(client, queries, how=search):
    all_results = []
    for query in queries.to_dict(orient='records'):
        print(f"Searching for {query['QueryId']},{query['Query']}")
        results = how(client, query['Query'])
        for rank, result in enumerate(results):
            source = result['_source']
            if rank == 0:
                if 'titleTag' in source:
                    print(source['titleTag'])
                else:
                    print("No title tag")
                if 'first_line' in source:
                    print(source['first_line'])
                else:
                    print("No first_line")
                    
                if 'remaining_lines' in source:
                    print(source['remaining_lines'])
                    
            source['rank'] = rank
            source['score'] = result['_score']
            source['DocumentId'] = source['id']
            source['QueryId'] = query['QueryId']
            all_results.append(source)
        print()
        print()
    all_results = pd.DataFrame(all_results)
    return queries.merge(all_results, how='left', on='QueryId').sort_values(['QueryId', 'rank'])
    
submission = search_all(client, queries.sample(frac=1.0))
submission

Searching for 1741,how to restart vsphere web client service
No title tag
In the vSphere Web Client, you can start, stop, and restart services that are running on vCenter Server.
['You can restart services upon a configuration change or in case of suspected functional or performance issues.', 'Prerequisites', 'Verify that the user you use to log in to the vCenter Server instance is a member of the SystemConfiguration.Administrators group in the vCenter Single Sign-On domain.', 'Procedure', 'Log in to the vCenter Server by using the vSphere Web Client.', 'On the vSphere Web Client Home page, click System Configuration.', 'Under System Configuration click Services.', 'From the Services list select a manageable service.', 'From the Actions menu select an operation name.', 'Restart', 'Start', 'Stop', 'Note: Restarting the Content Library Service also restarts the Transfer Service and the OVF Service.', 'The Content Library Service, the Transfer Service, and the OVF Service run on the same 

Troubleshooting permissions errors when connecting to vCenter Server with the vSphere Client (1003872) | VMware KB
Troubleshooting permissions errors when connecting to vCenter Server with the vSphere Client (1003872) | VMware KB
['Troubleshooting permissions errors when connecting to vCenter Server with the vSphere Client (1003872)', 'Symptoms', 'Login to vCenter Server fails.', 'You see an error similar to:', 'Unable to login because you do not have permission on any vCenter Server systems connected to this client', 'Purpose', 'This article provides steps to:', 'Troubleshoot permissions issues that are preventing log in to vCenter Server.', 'Test if you have an authentication issue.', 'Resolve problems with authentication.', 'Cause', 'This issue occurs due to the user account (Active Directory user or a Local User) does not have the appropriate permissions to log in to vCenter Server.', 'By default, the local administrators group on the vCenter Server is the only group that has acces

"[400] An error occurred while sending an authentication request" while logging in to vSphere Client using the vCenter Server shortname (71387) | VMware KB
"[400] An error occurred while sending an authentication request" while logging in to vSphere Client using the vCenter Server shortname (71387) | VMware KB
['"[400] An error occurred while sending an authentication request" while logging in to vSphere Client using the vCenter Server shortname (71387)', 'Symptoms', 'Logging onto vSphere Client using the vCenter Server shortname results in the following error:', '[400] An error occurred while sending an authentication request to the vCenter Single Sign-On server- An error occurred when processing meta data during vCenter Single Sign-On setup:the service provider validation failed.', 'Verify that the server URL is correct and is in FQDN format, or that the hostname is a trusted service provider alias.', 'Issue is not observed while using the Fully Qualified Domain Name (FQDN) or IP add

What is Desktop Virtualization? | VMware Glossary
What is Desktop Virtualization? | VMware Glossary
['Desktop Virtualization', 'What is Desktop Virtualization?', 'Desktop virtualization is a method of simulating a user workstation so it can be accessed from a remotely connected device.', 'By abstracting the user desktop in this way, organizations can allow users to work from virtually anywhere with a network connecting, using any desktop laptop, tablet, or smartphone to access enterprise resources without regard to the device or operating system employed by the remote user.', 'Remote desktop virtualization is also a key component of digital workspaces.', 'Virtual desktop workloads run on desktop virtualization servers which typically execute on virtual machines (VMs) either at on-premises data centers or in the public cloud.', 'Download Now', 'Since the user devices is basically a display, keyboard, and mouse, a lost or stolen device presents a reduced risk to the organization.', 'All 

No title tag
You must take a snapshot of the AppDefense Appliance virtual machine (VM) before the upgrade.
['During the AppDefense Appliance upgrade, RPMs are installed and database migration occurs in the Appliance VM.', 'The AppDefense Appliance do not have any automatic backup and restore feature.', 'If upgrade fails, you can preserve the state of the Appliance VM.', 'Procedure', 'Right-click the AppDefense Appliance virtual machine and select Snapshots>Take Snapshot.', 'For details, refer to the vSphere Documentation.', 'Upgrade based on your configured Appliance upgrade strategy.', 'If the upgrade is successful, you can delete the snapshot as per the space requirement.', 'If the upgrade fails, revert the VM to the snapshot taken before upgrade.']


Searching for 1599,what is true about virtualization
What is True Visibility in Your IT stack? - VMware Cloud Management
What is True Visibility in Your IT stack? - VMware Cloud Management
['Share on:Share on Twitter', 'Share on LinkedI

...

Upgrading VMware Tools without reinstalling VSS and Sync Driver (1037307) | VMware KB
Upgrading VMware Tools without reinstalling VSS and Sync Driver (1037307) | VMware KB
['Upgrading VMware Tools without reinstalling VSS and Sync Driver (1037307)', 'Symptoms', 'When you upgrade VMware Tools, VMware VSS and Sync Driver are automatically reinstalled.', 'However, some backup applications require you to remove VSS provider and Sync Driver.', 'This article provides steps to upgrade VMware Tools without reinstalling VSS and Sync Driver.', 'install-vmware-tools vmware-tools-install-upgrade-fails vmware-tools-upgrade-fails', 'Resolution', 'To upgrade VMware Tools without reinstalling VSS and Sync Driver:', 'Mount the VMware Tools installer.', 'Click Start>Run, type cmd, and click OK.', 'This opens the Command Prompt window.', 'Run this command to change directory to the CD-ROM drive:', 'cd D:', 'Run this command to upgrade VMware Tools without reinstalling VSS and Sync Driver:', 'msiexec /Fvo

How to Run Kali Linux on All VMware Platforms - VMware Customer Experience and Success
How to Run Kali Linux on All VMware Platforms - VMware Customer Experience and Success
['Share on:Share on Twitter', 'Share on LinkedIn', 'Share on Facebook', 'Email this post', 'How to Run Kali Linux on All VMware Platforms', 'Kali Linux is a popular and powerful Linux distribution that comes with many security tools built right in.', 'If you have ever head of BackTrack, BackTrack became Kali Linux in 2013.', 'It is a Debian based distribution.', 'A distribution like Kali is important for security professionals because it comes with so many tools baked into [...]', 'Blog Name: Melissa Palmer', 'Published on 2019-12-10 | Time 16:00:28', 'Related Articles', 'Multi-CloudMoving to Cloud: Simple, But Not Easy', 'Andrea Siviero', 'May 20, 2021', 'Digital Workspace3 Key Operational Considerations to Support an Anywhere Workforce', 'Kelly Masters', 'April 29, 2021', 'Customer SuccessAutomation in Customer S

"An error occurred while sending an authentication request to the PSC Single Sign-On server - null" while connecting to PSC Client after upgrading vCenter Server to 6.5 (52541) | VMware KB
"An error occurred while sending an authentication request to the PSC Single Sign-On server - null" while connecting to PSC Client after upgrading vCenter Server to 6.5 (52541) | VMware KB
['"An error occurred while sending an authentication request to the PSC Single Sign-On server - null" while connecting to PSC Client after upgrading vCenter Server to 6.5 (52541)', 'Symptoms', 'After upgrading vCenter Server, connecting to the Platform Service Controller UI https://PSC-FQDN/PSC fails with the error:', 'HTTP Status 400 - An error occurred while sending an authentication request to the PSC Single Sign-On server - null', 'type Status report', 'message An error occurred while sending an authentication request to the PSC Single Sign-On server - null', 'description The request sent by the client was synt

No title tag
VM Monitoring restarts individual virtual machines if their VMware Tools heartbeats are not received within a set time.
['Similarly, Application Monitoring can restart a virtual machine if the heartbeats for an application it is running are not received.', 'You can enable these features and configure the sensitivity with which vSphere HA monitors non-responsiveness.', 'When you enable VM Monitoring, the VM Monitoring service (using VMware Tools) evaluates whether each virtual machine in the cluster is running by checking for regular heartbeats and I/O activity from the VMware Tools process running inside the guest.', 'If no heartbeats or I/O activity are received, this is most likely because the guest operating system has failed or VMware Tools is not being allocated any time to complete tasks.', 'In such a case, the VM Monitoring service determines that the virtual machine has failed and the virtual machine is rebooted to restore service.', 'Occasionally, virtual machines

QueryId                           Query  type subject  \
5595        0              what is hypervisor   NaN     NaN   
5596        0              what is hypervisor   NaN     NaN   
5597        0              what is hypervisor   NaN     NaN   
5598        0              what is hypervisor   NaN     NaN   
5599        0              what is hypervisor   NaN     NaN   
...       ...                             ...   ...     ...   
4030     2350  kubernetes what is a namespace   NaN     NaN   
4031     2350  kubernetes what is a namespace  task           
4032     2350  kubernetes what is a namespace  task           
4033     2350  kubernetes what is a namespace  task           
4034     2350  kubernetes what is a namespace  task           

                                                  title abstract  \
5595            What is a Hypervisor? | VMware Glossary      NaN   
5596  What is a vSphere Hypervisor? | Free Hyperviso...      NaN   
5597      What is a Cloud Hypervisor? | VMware Glossary      NaN   
5598  What is a Bare Metal Hypervisor? | VMware Glos...      NaN   
5599  What is ESXI? | Bare Metal Hypervisor | ESX | ...      NaN   
...                                                 ...      ...   
4030  What is a Kubernetes Namespace? | VMware Glossary      NaN   
4031      Configure a Kubernetes Zone in Cloud Assembly            
4032  Configure a Kubernetes Zone in vRealize Automa...            
4033  Configure a Kubernetes Zone in vRealize Automa...            
4034  Configure a Kubernetes Zone in vRealize Automa...            

                                            description  \
5595  Hypervisor, also known as a virtual machine mo...   
5596  vSphere Hypervisor is a bare-metal hypervisor ...   
5597  A Cloud Hypervisor is software that enables th...   
5598  The bare metal hypervisor is the most commonly...   
5599  VMware ESXi formerly known as ESX is a bare me...   
...                                                 ...   
4030  Namespaces are a way to organize clusters into...   
4031  Kubernetes zones enable cloud administrators t...   
4032  Kubernetes zones enable cloud administrators t...   
4033  Kubernetes zones enable cloud administrators t...   
4034  Kubernetes zones enable cloud administrators t...   

                             keywords  \
5595                              NaN   
5596  vsphere hypervisor, hypervisor,   
5597                              NaN   
5598                              NaN   
5599      bare metal hypervisor, ESXI   
...                               ...   
4030                              NaN   
4031                                    
4032                                    
4033                                    
4034                                    

                                           guid format  ... datePublished  \
5595                                        NaN    NaN  ...    11-09-2020   
5596                                        NaN    NaN  ...           NaN   
5597                                        NaN    NaN  ...    02-19-2021   
5598                                        NaN    NaN  ...    12-21-2020   
5599                                        NaN    NaN  ...           NaN   
...                                         ...    ...  ...           ...   
4030                                        NaN    NaN  ...    11-18-2020   
4031  GUID-25F66F7C-9502-4343-8E44-D02EDE1EB8E2  HTML5  ...           NaN   
4032  GUID-25F66F7C-9502-4343-8E44-D02EDE1EB8E2  HTML5  ...           NaN   
4033  GUID-25F66F7C-9502-4343-8E44-D02EDE1EB8E2  HTML5  ...           NaN   
4034  GUID-25F66F7C-9502-4343-8E44-D02EDE1EB8E2  HTML5  ...           NaN   

     uberflip:hub_id application-name msapplication-starturl  \
5595             NaN              NaN                    NaN   
5596             NaN              NaN                    NaN   
5597             NaN              NaN                    NaN   
5598             NaN              NaN            

In [3]:
def write_submission(submission='pull_out_firstline'):
    from time import time
    timestamp = str(time()).replace('.', '')
    fname = f'data/turnbull_submission_{timestamp}.csv'
    print("Writing To: ", fname)
    submission[['QueryId', 'DocumentId']].to_csv(fname, index=False)

In [72]:
write_submission()

Writing To:  data/turnbull_submission_1652544680901428.csv


In [57]:
corpus[corpus['id'].str.contains('https---blogs.vmware.com-cloudprovider-2015-11-simplifying-cloud-spending-with-vmware-subscription-purchase-program.txt')]

onetrust-data-domain  \
11041  b9242434-9feb-47be-a894-3a9e658fdd50   

                                         microsites-utag  \
11041  https://tags.tiqcdn.com/utag/vmware/microsites...   

                                                titleTag csrf-param  \
11041  Simplifying Cloud Spending with VMware Subscri...        NaN   

      csrf-token DC.Title DC.Subject DC.Language google-site-verification  \
11041        NaN      NaN        NaN         NaN                      NaN   

      facebook-domain-verification  ... machine-translated name custom_label  \
11041                          NaN  ...                NaN  NaN          NaN   

      link_url children  url lastModified  md5 publication-author-name  \
11041      NaN      NaN  NaN          NaN  NaN                     NaN   

      output-file-name  
11041              NaN  

[1 rows x 90 columns]

In [18]:
es = client.es
body = {
    'size': 5,
    'query': {
        'match_all': {
        }
    },
    'aggs': {
        'doc_group': {
            'terms': {'field': 'document_group'}
        }
    }
}
for doc in es.search(index='vmware', body=body)['hits']['hits']:
    print(doc['_source']['title'])
    print(doc['_source'].keys())

RequestError: RequestError(400, 'search_phase_execution_exception', 'Text fields are not optimised for operations that require per-document field data like aggregations and sorting, so these operations are disabled by default. Please use a keyword field instead. Alternatively, set fielddata=true on [document_group] in order to load field data by uninverting the inverted index. Note that this can use significant memory.')

In [ ]:
from 